In [11]:
import pandas as pd
import nltk
import jellyfish
import pycountry
import re

dataset = pd.read_csv('../Procesamiento_Datos/full-data.csv')

In [171]:
dataset.shape

(7809, 40)

In [12]:
df_locations = dataset[['user_location']]

In [13]:
df_locations.rename({'user_location': 'original_location'}, axis=1, inplace=True)
df_locations

/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/pandas/core/frame.py:4438: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().rename(


original_location
0             Stockholm, Sweden
1     Namibia, Okaanga village 
2                Leeds, England
3                           NaN
4                           NaN
...                         ...
7804                        NaN
7805                        NaN
7806                        NaN
7807                        NaN
7808              Colorado, USA

[7809 rows x 1 columns]

**Hacemos un primer barrido rápido para buscar si hay algun nombre de pais en el localización y lo guardamos en la columna 'search_country_1'**

In [15]:
exceptions = [('New\sYork', 'United States'), ('Los\sAngeles', 'United States'), 
                ('San\sFrancisco', 'United States'), ('Buenos\sAires', 'Argentina'), 
                ('Cape\sTown', 'South Africa'), ('San\sDiego', 'United States'), 
                ('Rio\sDe\sJaneiro', 'Brazil'), ('Nyc', 'United States'),('Newyork', 'United States'), ('Ny', 'United States'), 
                ('Washington\sDc', 'United States'), ('Scotland', 'United Kingdom'),
                ('Wales', 'United Kingdom'),('England', 'United Kingdom'), ('Dc', 'United States'), 
                ('Usa', 'United States'), ('Us', 'United States'), ('Uk', 'United Kingdom'), ('Queensland', 'Australia')]

In [16]:
us_states = ["Alabama","Alaska","Arizona","Arkansas","California","Colorado","Connecticut","Delaware","Florida","Georgia","Hawaii","Idaho","Illinois",
  "Indiana","Iowa","Kansas","Kentucky","Louisiana","Maine","Maryland","Massachusetts","Michigan","Minnesota","Mississippi","Missouri","Montana",
  "Nebraska","Nevada","New\sHampshire","New\sJersey","New\sMexico","New\sYork","North\sCarolina","North\sDakota","Ohio","Oklahoma","Oregon","Pennsylvania",
  "Rhode\sIsland","South\sCarolina","South\sDakota","Tennessee","Texas","Utah","Vermont","Virginia","Washington","West\sVirginia","Wisconsin","Wyoming", 
  'Al', 'Ak', 'Az', 'Ar', 'Ca', 'Co', 'Ct', 'Dc', 'De', 'Fl', 'Ga', 'Hi', 'Id', 'Il', 'In', 'Ia', 'Ks', 'Ky', 'La', 'Me', 'Md', 'Ma', 'Mi', 'Mn', 'Ms', 
  'Mo', 'Mt', 'Ne', 'Nv', 'Nh', 'Nj', 'Nm', 'Ny', 'Nc', 'Nd', 'Oh', 'Ok', 'Or', 'Pa', 'Ri', 'Sc', 'Sd', 'Tn', 'Tx', 'Ut', 'Vt', 'Va', 'Wa', 'Wv', 'Wi', 'Wy']

In [17]:
def find_country(text, exceptions):
    x = 'NA'
    text = str(text).title()
    #buscar excepciones
    for i in exceptions:
        s = re.search(i[0], text)
        if s != None:
            x = i[1]
            break

    #buscar US States
    for i in us_states:
        s = re.search(i, text)
        if s != None:
            x = 'United States'
            break

    #buscar paises
    for country in pycountry.countries:
        if country.name in text:
            x = country.name

    return x


In [18]:
df_locations['search_country_1'] = df_locations['original_location'].apply(lambda x: find_country(x, exceptions))

<ipython-input-18-758e2ccc2b5f>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_locations['search_country_1'] = df_locations['original_location'].apply(lambda x: find_country(x, exceptions))


In [19]:
df_locations

original_location search_country_1
0             Stockholm, Sweden           Sweden
1     Namibia, Okaanga village           Namibia
2                Leeds, England   United Kingdom
3                           NaN               NA
4                           NaN               NA
...                         ...              ...
7804                        NaN               NA
7805                        NaN               NA
7806                        NaN               NA
7807                        NaN               NA
7808              Colorado, USA    United States

[7809 rows x 2 columns]

**A continuación, tratamos de encontrar nombres de ciudades. Para ello importamos un BBDD de ciudades del mundo**

In [20]:
#ATENCIÓN!! Esta linea dará error! El archivo es muy grande y github no lo acepta --> Contactar con Mario 

list_cities = pd.read_csv('/Users/mariomartinezazcona/Desktop/worldcitiespop.csv')

/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/IPython/core/interactiveshell.py:3165: DtypeWarning: Columns (3) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


In [21]:
list_cities.drop(['Region'], inplace=True, axis=1)


Ordenamos el dataframe de mayor a menos poplacion para que en caso de ciudades con el mismo nombre, se escoja la primera

In [22]:
list_cities.sort_values(by='Population', ascending=False, inplace=True) 
list_cities.head()

Country       City AccentCity  Population   Latitude   Longitude
1544449      jp      tokyo      Tokyo  31480498.0  35.685000  139.751389
570824       cn   shanghai   Shanghai  14608512.0  31.045556  121.399722
1327914      in     bombay     Bombay  12692717.0  18.975000   72.825833
2200161      pk    karachi    Karachi  11627378.0  24.905600   67.082200
1349146      in  new delhi  New Delhi  10928270.0  28.600000   77.200000

Necesitamos añadir una columna a *list_cities* con el nombre del pais. Para ello definimos la siguiente función:

In [23]:
def get_country_name(code):
    try:
        return pycountry.countries.indices['alpha_2'][str(code)].name
    except:
        return '-'

In [25]:
country_table = pd.DataFrame(list_cities.Country.unique(), columns=['code'])
country_table['Country_name'] = country_table['code'].apply(lambda x: get_country_name(x))
country_table.head()

code Country_name
0   jp        Japan
1   cn        China
2   in        India
3   pk     Pakistan
4   ph  Philippines

In [26]:
list_cities = pd.merge(list_cities, country_table, left_on='Country', right_on='code', how='left')
list_cities.drop('code', axis=1, inplace=True)
list_cities = list_cities[['Country', 'Country_name', 'City', 'AccentCity', 'Population', 'Latitude', 'Longitude']]

In [27]:
list_cities.head()

Country Country_name       City AccentCity  Population   Latitude  \
0      jp        Japan      tokyo      Tokyo  31480498.0  35.685000   
1      cn        China   shanghai   Shanghai  14608512.0  31.045556   
2      in        India     bombay     Bombay  12692717.0  18.975000   
3      pk     Pakistan    karachi    Karachi  11627378.0  24.905600   
4      in        India  new delhi  New Delhi  10928270.0  28.600000   

    Longitude  
0  139.751389  
1  121.399722  
2   72.825833  
3   67.082200  
4   77.200000

In [28]:
list_cities[list_cities['City']=="medina del campo"]['Country_name'].head(1).item()

'Spain'

Función para limpiar texto antes de buscar ciudad:

In [186]:
def eliminar_tildes(texto):
    texto_limpio = re.sub('(á)|(Á)|(à)|(À)','a', texto)
    texto_limpio = re.sub('(é)|(É)|(è)|(È)','e', texto_limpio)
    texto_limpio = re.sub('(í)|(Í)|(ì)|(Ì)','i', texto_limpio)
    texto_limpio = re.sub('(ó)|(Ó)|(ò)|(Ò)','o', texto_limpio)
    texto_limpio = re.sub('(ú)|(Ú)|(ù)|(Ù)','u', texto_limpio)
    return texto_limpio



In [187]:
def find_city(text):
    
    text = str(text).lower() # Paso a minusculas
    text = eliminar_tildes(text) # Eliminar tildes
    text = re.sub(r'[^\w\s]','',text) # Eliminar puntuacion
    text = text.split() # Lista con cada palabra para que no capture partes de palabras como ciudades

    try:
        for city in list_cities.City:
            if city in text:
                return city
                break
    except:
        return '-'


In [188]:
def city_to_country(city):
    try:
        return list_cities[list_cities['City']==str(city)]['Country_name'].head(1).item()
    except:
        return '-'

In [189]:
df_locations['search_city_1'] = df_locations['original_location'].apply(lambda x: find_city(x))

<ipython-input-189-30cdf458567c>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_locations['search_city_1'] = df_locations['original_location'].apply(lambda x: find_city(x))


In [190]:
df_locations['search_city_1_country'] = df_locations['search_city_1'].apply(lambda x: city_to_country(x))

<ipython-input-190-f1a8b2dbf8c3>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_locations['search_city_1_country'] = df_locations['search_city_1'].apply(lambda x: city_to_country(x))


In [191]:
df_locations.tail(50)

original_location search_country_1  search_city_1  \
7759              California, USA    United States     california   
7760                    pa carajo    United States             pa   
7761                  Spread Love               NA           love   
7762                          NaN               NA           None   
7763                Jersey and DC           Jersey            and   
7764                   Dallas, TX    United States         dallas   
7765          Only Just into Kent    United States           kent   
7766                       he/him    United States           None   
7767                         ATL                NA           None   
7768                          NaN               NA           None   
7769       San Francisco Bay Area    United States            bay   
7770                20 | she/her                NA           None   
7771             Independence, MO    United States   independence   
7772                 NYC, NY, USA    United States            usa   
7773                          NaN               NA           None   
7774                  Chicago, IL    United States        chicago   
7775                          NaN               NA           None   
7776             Bengaluru, India            India          india   
7777                          NaN               NA           None   
7778            Stockholm, Sweden           Sweden      stockholm   
7779                          NaN               NA           None   
7780                   he/him, 18    United States           None   
7781                          NaN               NA           None   
7782                          NaN               NA           None   
7783                         Сочи               NA           None   
7784              London, England   United Kingdom         london   
7785                Monmouthshire    United States  monmouthshire   
7786             Bengaluru, India            India          india   
7787                            🍔               NA           None   
7788            Nassau county, NY    United States         nassau   
7789             New Delhi, India            India          delhi   
7790                          NaN               NA           None   
7791              London, England   United Kingdom         london   
7792                 Bethesda, MD    United States       bethesda   
7793                  Chicago, IL    United States        chicago   
7794            New York/Delaware    United States            new   
7795                  Chicago, IL    United States        chicago   
7796                           UK   United Kingdom             uk   
7797                    Melbourne    United States      melbourne   
7798          @liltunechi's heart               NA          heart   
7799                      crawley               NA        crawley   
7800              London, England   United Kingdom         london   
7801  We$tside HARLEM, NYC x Cali    United States           cali   
7802                          ATL               NA           None   
7803                          NaN               NA           None   
7804                          NaN               NA           None   
7805                          NaN               NA           None   
7806                          NaN               NA           None   
7807                          NaN               NA           None   
7808                Colorado, USA    United States       colorado   

          search_city_1_country  
7759                   Colombia  
7760               Burkina Faso  
7761                     Angola  
7762                          -  
7763  Iran, Islamic Republic of  
7764              United States  
7765              United States  
7766                          -  
7767                          -  
7768                          -  
7769                Philippines  
7770                          -  
7771              United States  
7772                

In [192]:
def select_country(search_country_1, search_city_1_country):

    if search_country_1 == 'NA':
        return search_city_1_country
    else:
        return search_country_1
    
df_locations['country'] = df_locations[['search_country_1', 'search_city_1_country']].apply(lambda x: select_country(*x), axis=1)

<ipython-input-192-069ddf759636>:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_locations['country'] = df_locations[['search_country_1', 'search_city_1_country']].apply(lambda x: select_country(*x), axis=1)


In [193]:
def highlight_cols(s):
    return 'background-color: % s' % 'yellow'
  
df_locations.style.applymap(highlight_cols,subset = pd.IndexSlice[:, ['country']])


In [194]:
dataset['final_location'] = df_locations['country']

In [195]:
dataset.to_csv('../Procesamiento_Datos/full-data.csv')

In [197]:
dataset.head()

Unnamed: 0  Unnamed: 0.1  Unnamed: 0.1.1  \
0           0             0               0   
1           1             1               1   
2           2             2               2   
3           3             3               3   
4           4             4               4   

                                                text  created_at  \
0  @Uber_Support hi guys why all my trips this we...  Wed Aug 11   
1  So are we getting Uber eats league 1 or not @S...  Wed Aug 11   
2  @footballdaily 2-3 years of Messi, a bit of ca...  Wed Aug 11   
3  @Prashan32439454 @Uber_Support @rameshjoshi80 ...  Wed Aug 11   
4  Uber's Gopuff partnership, Drizly deal being p...  Wed Aug 11   

  created_at_time  created_at_hour retweeted  retweet_count  favorite_count  \
0        09:43:42                9        Si              1               0   
1        09:43:39                9        No              0               0   
2        09:43:36                9        No              0               0   
3        09:43:36                9        No              0               0   
4        09:43:33                9        No              0               0   

   ...                                         categories  topic_1  \
0  ...  [{'score': 0.693098, 'label': '/travel/special...   travel   
1  ...  [{'score': 0.59693, 'label': '/sports/baseball...   sports   
2  ...   [{'score': 0.785107, 'label': '/sports/soccer'}]   sports   
3  ...  [{'score': 0.685688, 'label': '/science/mathem...  science   
4  ...  [{'score': 0.778195, 'label': '/news'}, {'scor...     news   

            topic_2           topic_3  emoji_list  sent_emoji_pos  \
0  specialty travel  adventure travel          []             0.0   
1          baseball               NaN          []             0.0   
2            soccer               NaN          []             0.0   
3       mathematics        arithmetic          []             0.0   
4               NaN               NaN          []             0.0   

   sent_emoji_neu sent_emoji_neg  emoji_unicode  final_location  
0             0.0            0.0             []          Sweden  
1             0.0            0.0             []         Namibia  
2             0.0            0.0             []  United Kingdom  
3             0.0            0.0             []               -  
4             0.0            0.0             []               -  

[5 rows x 42 columns]

Obtención Longitud y Latitud:

In [43]:
def get_latitude(country):
    try:
        if country == '-':
             return 'NA'
        else:
            return list_cities[list_cities['Country_name']==str(country)]['Latitude'].head(1).item()
    except:
        return 'NA'

def get_longitude(country):
    try:
        if country == '-':
            return 'NA'
        else:
            return list_cities[list_cities['Country_name']==str(country)]['Longitude'].head(1).item()
    except:
        return 'NA'

In [46]:
df = dataset

In [47]:
df['Latitude'] = df['final_location'].apply(get_latitude)
df['Longitude'] = df['final_location'].apply(get_longitude)

In [45]:
df

Unnamed: 0  Unnamed: 0.1  Unnamed: 0.1.1  \
0            0             0               0   
1            1             1               1   
2            2             2               2   
3            3             3               3   
4            4             4               4   
..         ...           ...             ...   
95          95            95              95   
96          96            96              96   
97          97            97              97   
98          98            98              98   
99          99            99              99   

                                                 text  created_at  \
0   @Uber_Support hi guys why all my trips this we...  Wed Aug 11   
1   So are we getting Uber eats league 1 or not @S...  Wed Aug 11   
2   @footballdaily 2-3 years of Messi, a bit of ca...  Wed Aug 11   
3   @Prashan32439454 @Uber_Support @rameshjoshi80 ...  Wed Aug 11   
4   Uber's Gopuff partnership, Drizly deal being p...  Wed Aug 11   
..                                                ...         ...   
95  @Ligue1_ENG @PSG_English Can I use “Messi” as ...  Wed Aug 11   
96  Doctors Appointment App Like Uber \nhttps://t....  Wed Aug 11   
97  @SidityDes I trade &amp; Uber on the side. Plu...  Wed Aug 11   
98  @Uber_India @Uber @Uber_Support Me and my husb...  Wed Aug 11   
99  @NazneenTowhid @thephukdi @GaurangBhardwa1 Do ...  Wed Aug 11   

   created_at_time  created_at_hour retweeted  retweet_count  favorite_count  \
0         09:43:42                9        Si              1               0   
1         09:43:39                9        No              0               0   
2         09:43:36                9        No              0               0   
3         09:43:36                9        No              0               0   
4         09:43:33                9        No              0               0   
..             ...              ...       ...            ...             ...   
95        09:31:29                9        No              0               0   
96        09:31:15                9        No              0               0   
97        09:31:11                9        No              0               0   
98        09:31:02                9        Si              1               0   
99        09:31:00                9        Si              1               0   

    ...                   topic_2           topic_3 emoji_list sent_emoji_pos  \
0   ...          specialty travel  adventure travel         []            0.0   
1   ...                  baseball               NaN         []            0.0   
2   ...                    soccer               NaN         []            0.0   
3   ...               mathematics        arithmetic         []            0.0   
4   ...                       NaN               NaN         []            0.0   
..  ...                       ...               ...        ...            ...   
95  ...  buying and selling homes               NaN         []            0.0   
96  ...       internet technology    social network         []            0.0   
97  ...  buying and selling homes               NaN         []            0.0   
98  ...                auto parts               NaN         []            0.0   
99  ...                  hinduism               NaN         []            0.0   

    sent_emoji_neu  sent_emoji_neg  emoji_unicode  final_location   Latitude  \
0              0.0             0.0             []          Sweden  59.333333   
1              0.0             0.0             []         Namibia -22.570000   
2              0.0             0.0             []  United Kingdom  51.514125   
3              0.0             0.0             []               -         NA   
4              0.0             0.0             []               -         NA   
..             ...             ...            ...             ...        ...   
95             0.0             0.0             []   United States  40.714167   
96             0.0      